In [1]:
#The database was uploaded to drive and the drive was mounted on google colab
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
#The location of the database
database = "/content/drive/MyDrive/Humor,Hist,Media,Food"


In [3]:
#Imports used
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer 
import nltk
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Unzipping corpora/wordnet.zip.


True

In [4]:
#Define the stop words
stop_words = set(stopwords.words('english'))

In [5]:
#This function is used to preprocess the text
def preprocess(text):
    #Convert text to lower
    text = text.lower()

    #Remove punctuations
    tokenizer = nltk.RegexpTokenizer(r"\w+")
    arr = tokenizer.tokenize(text)

    #Remove the stop words
    arr = [w for w in arr if not w in stop_words]

    #The spaces are removed in tokenisation function

    return arr

In [6]:
#This creates positional index
#Input are the gloabl dictionary "pos_idx",The tokenised "arr" and the current document number (doc_num)
def createPositionalIndex(arr,pos_idx,doc_num):
    for pos,term in enumerate(arr):
        if term in pos_idx:
            pos_idx[term][0] += 1                          #update the frequency of the word

            if doc_num in pos_idx[term][1]:
                pos_idx[term][1][doc_num].append(pos)      #if the doc_num of the word exist add the position
            else:
                temp_list = [pos]
                pos_idx[term][1][doc_num] = temp_list      #if the doc_num of the word doestnt exist create it
        else:
            temp_list = [1,{doc_num: [pos]}]
            pos_idx[term] = temp_list                      #if the term doesnt exist, initialise the frequency and the dictionary



In [7]:
import os
# assign directory
directory = database
pos_idx = {}            #This stores the positional index
doc_num = 0
file_dic = {}           #This stores the file names as value and doc_num as key
for filename in os.listdir(directory):
    f = os.path.join(directory, filename)
    if os.path.isfile(f):

        file1 = open(f,errors="ignore") 

        text = file1.read()
        
        #Preprocess
        arr = preprocess(text)

        #Create positional index
        createPositionalIndex(arr,pos_idx,doc_num)
        
        #Assign Doc_num to file name
        file_dic[doc_num] = f
        doc_num += 1

        file1.close()

In [8]:
pos_idx

{'rinaldo': [5, {0: [0], 417: [45, 88], 514: [1, 10]}],
 'laws': [158,
  {0: [1, 22],
   8: [29, 56, 59, 62, 128, 146, 158, 240, 266, 317, 533],
   19: [1],
   24: [1],
   28: [956],
   47: [1,
    195,
    361,
    368,
    377,
    384,
    391,
    400,
    409,
    421,
    432,
    445,
    1311,
    1648,
    1657,
    1667,
    1673,
    1683,
    1694,
    1707,
    1717,
    1725,
    1734,
    1743,
    1753,
    1764,
    1776,
    1786,
    1799],
   86: [451],
   112: [1184],
   124: [319],
   127: [878],
   168: [84, 88, 90, 92, 105],
   169: [63],
   209: [1],
   259: [1832],
   265: [49],
   292: [475],
   337: [596],
   354: [397],
   357: [9, 372, 397, 464],
   372: [192, 358],
   412: [518],
   417: [46, 89, 110],
   437: [103, 113],
   451: [751],
   491: [7, 651, 1987, 2675, 2813, 2928],
   514: [2, 11, 32],
   528: [1006, 1244, 1333, 1599],
   550: [2616],
   566: [50],
   570: [3990],
   574: [2930],
   575: [637, 2274, 3213, 3226],
   673: [189, 313],
   690: [2

In [16]:
#--------------------------------------Query--------------------------------#
query = input()
result = {}
count = 0
query_arr = preprocess(query)  #This processes the query
def find_doc(query):
    global result
    global count
    for word in query:
        try:
            current_dic = pos_idx[word][1]
        except:
            print("No doc found")
            break
        if(len(result) == 0):
            result = current_dic 
        else:
            set_result = set(result.keys())
            common_docs = set_result.intersection(set(current_dic.keys()))      #This is the intersection of docs between the final resultant 
            dic = {}                                                            #dictionary and the current selected word docs
            for doc_id in common_docs:
                dic[doc_id] = result[doc_id]
            if(len(common_docs)) == 0:
                print("No doc found")
                break
            result = dic                                                        #This is the resultant based on the same docs
            for doc_id in common_docs:
                #iterate over the posting list
                
                inc_list = [x+count for x in result[doc_id]]
                temp_pos = set(current_dic[doc_id]).intersection(set(inc_list)) #This finds the position in accordance to query
            
                if len(temp_pos) == 0:                                          #if No position is found for the current word in the doc, delete it
                    del result[doc_id]
            
        count += 1



find_doc(query_arr)             #Calling the function


Naman
No doc found


In [11]:
result

{215: [53], 1008: [8624, 21472, 21640], 1030: [53]}

In [12]:
names = []
for key in result.keys():
    print(key)
    names.append(file_dic[key])


1030
215
1008


In [15]:
print("The number of docs found are ",len(names))

The number of docs found are  3


In [13]:
names

['/content/drive/MyDrive/Humor,Hist,Media,Food/abbott.txt',
 '/content/drive/MyDrive/Humor,Hist,Media,Food/whoon1st.hum',
 '/content/drive/MyDrive/Humor,Hist,Media,Food/mlverb.hum']